In [193]:
# Administrative stuff:
import os

# For Data manipulation:
import pandas as pd
import numpy as np
import random
import re

# Nice to haves
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point, Polygon
# import googlemaps
import plotly.graph_objects as go

## dynamic text updating
from IPython.display import Markdown as md

## repeated printouts
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

# Getting Data from the Cleaning File

In [194]:
%store -r air_data
%store -r air_ken
%store -r air_ken_2019
%store -r health_county_names
%store -r health_data
%store -r health_ken
%store -r health_ken_2019
%store -r health_ken_2019_clean
%store -r health_ken_2019_fm
%store -r so2
%store -r so2_county_names
%store -r so2_ken
%store -r airq_0

no stored variable or alias airq_0


In [15]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)


# Merging air and Health Data First

In [16]:
air_ken_2019.head(2)
health_ken_2019_fm.head(2)

index     State County  Year  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10
0    326  Kentucky   Bell  2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0
1    327  Kentucky  Boone  2019            239        222             17                                    0               0                    0               0       80                   49          39        0         0         239           0          0

index  Year CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
0   3596  2019      Adair       21001  Health Risk Behaviors  No leisure-time physical activity among adults...               %  Crude prevalence        44.8           3,016  POINT (-85.15821669 37.13121962)  21001970300         LPA
2   3598  2019   Anderson       21005        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        26.6           5,372  POINT (-84.92306901 38.02049683)  21005950201  DEPRESSION

In [19]:
health_ken_2019_fm[health_ken_2019_fm["CountyName"] == "Jefferson"]

index  Year CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
53       3649  2019  Jefferson       21111        Health Outcomes  Cancer (excluding skin cancer) among adults ag...               %  Crude prevalence         6.1           2,924  POINT (-85.78202288 38.27661851)  21111000200      CANCER
55       3651  2019  Jefferson       21111             Prevention  Current lack of health insurance among adults ...               %  Crude prevalence        17.2           2,447   POINT (-85.78253076 38.2614617)  21111002300     ACCESS2
58       3654  2019  Jefferson       21111  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        15.9           6,253    POINT (-85.52422538 38.234524)  21111010402    CSMOKING
59       3655  2019  Jefferson       21111        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        21.3           3,078  POINT (-85.64078951 38.24198879)  21111010601  DEPRESSION
13421  825740  2019  Jefferson       21111             Prevention  Current lack of health insurance among adults ...               %  Crude prevalence         7.7           5,222  POINT (-85.56243511 38.15331331)  21111011519     ACCESS2
...       ...   ...        ...         ...                    ...                                                ...             ...               ...         ...             ...                               ...          ...         ...
29453  841817  2019  Jefferson       21111  Health Risk Behaviors  No leisure-time physical activity among adults...               %  Crude prevalence        51.4           2,540  POINT (-85.80521343 38.24337925)  21111001000         LPA
29458  841822  2019  Jefferson       21111          Health Status  Mental health not good for >=14 days among adu...               %  Crude prevalence        10.9           4,078  POINT (-85.57559354 38.25625142)  21111010102       MHLTH
29459  841823  2019  Jefferson       21111             Prevention  Visits to doctor for routine checkup within th...               %  Crude prevalence        81.3           6,220  POINT (-85.58511499 38.17750746)  21111011110     CHECKUP
29465  841829  2019  Jefferson       21111          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        10.2           1,949   POINT (-85.69251985 38.2569818)  21111007601       PHLTH
29466  841830  2019  Jefferson       21111  Health Risk Behaviors  No leisure-time physical activity among adults...               %  Crude prevalence        35.7           3,168  POINT (-85.89388157 38.10694993)  21111012103         LPA

[2280 rows x 13 columns]

In [36]:
health_ken_2019_fm[health_ken_2019_fm["CountyName"] == "Washington"]

index  Year  CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
127      3723  2019  Washington       21229             Prevention  Taking medicine for high blood pressure contro...               %  Crude prevalence        78.4           2,245  POINT (-85.09204887 37.71934026)  21229930300       BPMED
29667  842694  2019  Washington       21229        Health Outcomes  Chronic obstructive pulmonary disease among ad...               %  Crude prevalence        11.3           2,767  POINT (-85.13311282 37.83975557)  21229930100        COPD
29781  843228  2019  Washington       21229          Health Status  Fair or poor self-rated health status among ad...               %  Crude prevalence        25.4           2,767  POINT (-85.13311282 37.83975557)  21229930100       GHLTH
29871  843648  2019  Washington       21229             Prevention  Current lack of health insurance among adults ...               %  Crude prevalence        11.4           2,767  POINT (-85.13311282 37.83975557)  21229930100     ACCESS2
29988  844157  2019  Washington       21229        Health Outcomes  Chronic obstructive pulmonary disease among ad...               %  Crude prevalence        10.7           2,245  POINT (-85.09204887 37.71934026)  21229930300        COPD
30110  844724  2019  Washington       21229             Prevention  Taking medicine for high blood pressure contro...               %  Crude prevalence        77.9           2,767  POINT (-85.13311282 37.83975557)  21229930100       BPMED
30251  845345  2019  Washington       21229        Health Outcomes        Current asthma among adults aged >=18 years               %  Crude prevalence         9.9           6,705   POINT (-85.2676149 37.71827025)  21229930200     CASTHMA
30554  846655  2019  Washington       21229        Health Outcomes  Cancer (excluding skin cancer) among adults ag...               %  Crude prevalence         7.7           2,245  POINT (-85.09204887 37.71934026)  21229930300      CANCER
30631  846945  2019  Washington       21229        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        24.3           6,705   POINT (-85.2676149 37.71827025)  21229930200  DEPRESSION
30728  847363  2019  Washington       21229  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        26.4           2,767  POINT (-85.13311282 37.83975557)  21229930100    CSMOKING
30843  847857  2019  Washington       21229  Health Risk Behaviors  No leisure-time physical activity among adults...               %  Crude prevalence        33.6           6,705   POINT (-85.2676149 37.71827025)  21229930200         LPA
30868  847992  2019  Washington       21229        Health Outcomes  Cancer (excluding skin cancer) among adults ag...               %  Crude prevalence         7.7           2,767  POINT (-85.13311282 37.83975557)  21229930100      CANCER
30995  848478  2019  Washington       21229  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        26.1           2,245  POINT (-85.09204887 37.71934026)  21229930300    CSMOKING
31004  848527  2019  Washington       21229          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        17.4           2,767  POINT (-85.13311282 37.83975557)  21229930100       PHLTH
31186  849325  2019  Washington       21229          Health Status  Mental health not good for >=14 days among adu...               %  Crude prevalence        17.3           2,245  POINT (-85.09204887 37.71934026)  21229930300       MHLTH
31220  849470  2019  Washington       21229          Health Status  Fair or poor self-rated health status among ad...               %  Crude prevalence        23.8           2,245  POI

In [45]:
chck = health_ken_2019_fm[health_ken_2019_fm["CountyName"].isin(air_ken_2019["County"])].groupby(["CountyName"]).agg(unique_geos = ("Geolocation", "nunique"), 
                                                                                                              cnts = ("Measure", "count")).reset_index()
sum(chck["cnts"])

6900

In [195]:
# Initial merge: 4282432 rows × 23 columns
# Next: 6768 rows 

# Merging:

merged_ah = pd.merge(air_ken_2019, health_ken_2019_fm, how = "left", left_on = "County", right_on = "CountyName",suffixes=('_air', '_health'))
merged_ah.head(2)

index_air     State County  Year_air  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10  index_health  Year_health CountyName  CountyFIPS         Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
0        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        774350         2019       Bell       21013  Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        30.6           1,896  POINT (-83.53196181 36.73527758)  21013960400  DEPRESSION
1        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809745         2019       Bell       21013    Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        25.1           1,896  POINT (-83.53196181 36.73527758)  21013960400       PHLTH

In [9]:
air_ken_2019.shape
health_ken_2019_fm.shape
merged_ah.shape

## This is a one-to-many match for Air to Health
# Now, the issue is that sulfure matches to too many rows and multiplies everything? 


(27, 19)

(13272, 13)

(6900, 32)

In [8]:
air_ken_2019[air_ken_2019["County"] == "Bell"]
health_ken_2019_clean[health_ken_2019_clean["CountyName"] == "Bell"]

index     State County  Year  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10
0    326  Kentucky   Bell  2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0

index  Year CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
3        3599  2019       Bell       21013        Health Outcomes                Stroke among adults aged >=18 years               %  Crude prevalence         5.8           5,150  POINT (-83.73909778 36.76433928)  21013960200      STROKE
4        3600  2019       Bell       21013        Health Outcomes                Stroke among adults aged >=18 years               %  Crude prevalence         5.5           2,381  POINT (-83.61861461 36.71356868)  21013960300      STROKE
5        3601  2019       Bell       21013        Health Outcomes                Stroke among adults aged >=18 years               %  Crude prevalence         5.3           2,849  POINT (-83.72538629 36.61758576)  21013960700      STROKE
191    774350  2019       Bell       21013        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        30.6           1,896  POINT (-83.53196181 36.73527758)  21013960400  DEPRESSION
255    809745  2019       Bell       21013          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        25.1           1,896  POINT (-83.53196181 36.73527758)  21013960400       PHLTH
265    809759  2019       Bell       21013        Health Outcomes  Coronary heart disease among adults aged >=18 ...               %  Crude prevalence        11.9           1,896  POINT (-83.53196181 36.73527758)  21013960400         CHD
284    809781  2019       Bell       21013        Health Outcomes  Coronary heart disease among adults aged >=18 ...               %  Crude prevalence        10.6           3,139  POINT (-83.81829927 36.66805338)  21013961100         CHD
311    809818  2019       Bell       21013  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        33.3           3,139  POINT (-83.81829927 36.66805338)  21013961100    CSMOKING
319    809827  2019       Bell       21013             Prevention  Visits to doctor for routine checkup within th...               %  Crude prevalence        80.7           4,747  POINT (-83.76654247 36.59758829)  21013960600     CHECKUP
366    809884  2019       Bell       21013        Health Outcomes        Current asthma among adults aged >=18 years               %  Crude prevalence        11.8           3,771  POINT (-83.76484451 36.64167333)  21013960800     CASTHMA
372    809893  2019       Bell       21013          Health Status  Mental health not good for >=14 days among adu...               %  Crude prevalence        21.2           2,381  POINT (-83.61861461 36.71356868)  21013960300       MHLTH
387    809912  2019       Bell       21013          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        28.1           4,747  POINT (-83.76654247 36.59758829)  21013960600       PHLTH
458    809997  2019       Bell       21013        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        32.5           2,564   POINT (-83.58378607 36.8540896)  21013960100  DEPRESSION
477    810022  2019       Bell       21013        Health Outcomes   High blood pressure among adults aged >=18 years               %  Crude prevalence        44.9           2,194  POINT (-83.65437527 36.64859962)  21013960500      BPHIGH
491    810041  2019       Bell       21013          Health Status  Fair or poor self-rated health status among ad...               %  Crude prevalence        41.2           4,747  POINT (-83.76654247 36.59758829)  21013960600       GHLTH
508    810062  2019       Bell       21013        Health Outcomes  Chronic kidney disease among adults aged >=18 ...               %  Crude prevalence         4.3           2,381  POINT (-83.61861461 

In [9]:
merged_ah.head()

index_air     State County  Year_air  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10  index_health  Year_health CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId
0        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        774350         2019       Bell       21013        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        30.6           1,896  POINT (-83.53196181 36.73527758)  21013960400  DEPRESSION
1        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809745         2019       Bell       21013          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        25.1           1,896  POINT (-83.53196181 36.73527758)  21013960400       PHLTH
2        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809818         2019       Bell       21013  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        33.3           3,139  POINT (-83.81829927 36.66805338)  21013961100    CSMOKING
3        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809827         2019       Bell       21013             Prevention  Visits to doctor for routine checkup within th...               %  Crude prevalence        80.7           4,747  POINT (-83.76654247 36.59758829)  21013960600     CHECKUP
4        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809884         2019       Bell       21013        Health Outcomes        Current asthma among adults aged >=18 years               %  Crude prevalence        11.8           3,771  POINT (-83.76484451 36.64167333)  21013960800     CASTHMA

# Cleaning SO2 Data Again

# pg 10 of AQI report (https://www.airnow.gov/sites/default/files/2018-04/aqi_brochure_02_14_0.pdf) 


We are using this for defining categories for sulfur aqi in categories

<div class="alert alert-block alert-warning">
    <b>SO2 Data Problem: </b> <br>
For each county, we have almost 246 days worth of data measurements. This means that each county matches 246 times over.
    <br>
    <br>
<b>Solution: </b> <br>
    Melt the table so that we have <b> one row </b>  for each county and we have columns as needed e.g
    
| County Name | Number of Good Days | Bad Days | ... | Min AQI for that county for the entire year | Max AQI | Avg AQI |
|-------------|---------------------|----------|-----|---------------------------------------------|---------|---------|    
    
<b>Exceptions:</b><br>
    <b>1. Jefferson:</b> <br>
    It has three different sites, within that one county. Should we keep these as is? How do we decide how to remove which and keep which? <br>
    <b>2.Washington:</b> <br>
    The issue here was that there's two different methods of collection (i.e. two values for POC: “Parameter Occurrence Code” which correpsond to two different "Event Types") <br>
    I suggest that we keep the data collection methods that's used in other counties as well, which is POC = 1 & Event Type = None. <br>
    As an added dimension, we could see how the two different data method collections differ in giving samples.
    
</div>

In [207]:
# Maddie's code of cleaning & Classifying
so2_ken_f=so2_ken.dropna(subset=["AQI"],how='all',inplace=False)
so2_ken.shape
so2_ken_f.shape
filter_method = lambda x: 'Good' if x < 50 else 'Moderate' if (x > 50 and x <= 100) else 'Unhealthy for Sensitive Groups' if (x > 100 and x <= 150) else "NA" if (x == "NaN") else "Unhealthy"



so2_ken_f["AQI_category"] = so2_ken_f["AQI"].apply(filter_method)
so2_ken_f[so2_ken_f["AQI_category"]=="Unhealthy"].tail(12)




(7776, 29)

(7776, 29)

State Code  County Code  Site Num  Parameter Code  POC  Latitude  Longitude  Datum Parameter Name          Sample Duration Pollutant Standard  Date Local   Units of Measure Event Type  Observation Count  Observation Percent  Arithmetic Mean  1st Max Value  1st Max Hour  AQI  Method Code Method Name Local Site Name                                      Address State Name County Name      City Name CBSA Name Date of Last Change AQI_category
170363          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-03-29  Parts per million   Included                 17                100.0         0.049647          0.054            10   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170367          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-02  Parts per million   Included                 17                100.0         0.050765          0.054            13   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170374          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-09  Parts per million   Included                 17                100.0         0.050706          0.054            14   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170383          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-18  Parts per million   Included                 17                100.0         0.049176          0.054            10   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170386          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-21  Parts per million   Included                 17                100.0         0.050000          0.054            15   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170389          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-24  Parts per million   Included                 17                100.0         0.045471          0.054            12   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170394          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-04-29  Parts per million   Included                 17                100.0         0.049882          0.054            14   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city       NaN          2021-11-01    Unhealthy
170483          21          229      9991           44201    2   37.7046   -85.0485  WGS84          Ozone  8-HR RUN AVG BEGIN HOUR  Ozone 8-hour 2015  2019-07-27  Parts per million   Included                 17                100.0         0.048647          0.054            11   50          NaN          -        Mackville  542 Wesley-Miller Rd, Harrodsburg, KY 40330   Kentucky  Washington  Not in a city  

In [208]:
# My own code for everything in the yellow box -> this can just be in the data exploration part of the final code
# Need to melt this

# Exploration: Seeing how dates, sites, POC differ across the countie
# chck = so2_ken_f.groupby("County Name").agg(n_dates = ("Date Local", "nunique"),
#                                                cnts = ("State Code", "count"),
#                                            n_sites = ("Site Num", "nunique"))
# chck
# My thoery is that all the rows are just entries for different dates therefore your row count should be the same as 
# unique dates count
# chck["oto"] = (chck["n_dates"] == chck["cnts"])
# chck[chck["oto"] == False]
# chck

# # Check Jefferson & Washington for exceptions
# Jefforson has three diferent sites -> how to merge these?
# Washington uses two different methods of collecting data -> that can be a good thing to explore e.g. 
# What are the variations for these different methods?
# For merginf purposes, we need to see which POC matches with other counties

# jeff_boi = so2_ken_f[so2_ken_f["County Name"] == "Jefferson"]
# jeff_boi["Date Local"].value_counts()
# jeff_boi[jeff_boi["Date Local"] == "2019-02-28"]
# morgan["Event Type"].value_counts()
# morgan["POC"].value_counts()
# jeff_boi["Event Type"].value_counts()
# jeff_boi["POC"].value_counts()
# wash_boi["Event Type"].value_counts()
# wash_boi["POC"].value_counts()
# wash_boi = so2_ken_f[so2_ken_f["County Name"] == "Washington"]
# wash_boi["Date Local"].value_counts()
# wash_boi[wash_boi["Date Local"] == "2019-01-01"]
# wash_boi[""]

In [209]:
# # Cleaning data for Washington
# # Count should go down by 365
# so2_ken_ff = so2_ken_f[so2_ken_f["Event Type"] != "Included"]
# # so2_ken_f["County Name"].value_counts()
# # so2_ken_ff["County Name"].value_counts()
# chck2 = so2_ken_ff.groupby("County Name").agg(n_dates = ("Date Local", "nunique"),
#                                                cnts = ("State Code", "count"),
#                                            n_sites = ("Site Num", "nunique"))
# chck2["oto"] = (chck2["n_dates"] == chck2["cnts"])
# chck2.reset_index()

In [210]:
# Condensing data -> We should have 25 + 3 (Jefferson) rows

so2_ken_ff["good_aqi"] = (so2_ken_ff["AQI_category"] == "Good")
so2_ken_ff["moderate_aqi"] = (so2_ken_ff["AQI_category"] == "Moderate")
so2_ken_ff["unhealthy_aqi"] = (so2_ken_ff["AQI_category"] == "Unhealthy")
so2_ken_ff["unhealthy_sens_aqi"] = (so2_ken_ff["AQI_category"] == "Unhealthy for Sensitive Groups")

so2_reshape = so2_ken_ff.groupby(["County Name", "Site Num"]).agg(so2_n_dates = ("Date Local", "count"),
                                                   so2_good_days = ("good_aqi", "sum"),
                                                  so2_moderate_days = ("moderate_aqi", "sum"),
                                                  so2_unhealthy_days = ("unhealthy_aqi", "sum"),
                                                                  so2_unhealthy_sens_days = ("unhealthy_sens_aqi", "sum"),
                                                                  so2_avg_aqi = ("AQI", "mean"),
                                                                  so2_max_aqi = ("AQI", "max"),
                                                                  so2_min_AQI = ("AQI", "min"))

In [212]:
# Adding long lat data
so2_reshape2 = pd.merge(pd.DataFrame(so2_ken_ff.groupby(["County Name", "Site Num", "Latitude", "Longitude"]).size().reset_index())
                        ,so2_reshape, how = "left", on = ["County Name", "Site Num"])

so2_reshape2 = so2_reshape2.drop([0], axis=1)
so2_reshape2.rename(columns={"Latitude": "so2_lat", "Longitude": "so2_long"}, inplace= True)

<div class="alert alert-block alert-warning">
Now we have almost a one-to-many merge of SO2 data with Air data <b> barring Jefferson </b>
    </div>

In [213]:
merged_ahs = pd.merge(merged_ah, so2_reshape2, how = "inner", left_on = "County", right_on = "County Name",suffixes=('_ah', '_Sulfur'))
merged_ahs.head(2)

index_air     State County  Year_air  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10  index_health  Year_health CountyName  CountyFIPS         Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId County Name  Site Num   so2_lat  so2_long  so2_n_dates  so2_good_days  so2_moderate_days  so2_unhealthy_days  so2_unhealthy_sens_days  so2_avg_aqi  so2_max_aqi  so2_min_AQI
0        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        774350         2019       Bell       21013  Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        30.6           1,896  POINT (-83.53196181 36.73527758)  21013960400  DEPRESSION        Bell         2  36.60843 -83.73694          246            228                 12                   6                        0    38.455285           77           14
1        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809745         2019       Bell       21013    Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        25.1           1,896  POINT (-83.53196181 36.73527758)  21013960400       PHLTH        Bell         2  36.60843 -83.73694          246            228                 12                   6                        0    38.455285           77           14

In [214]:
merged_ah.shape
so2_reshape.shape
merged_ahs.shape

(6900, 32)

(28, 8)

(11328, 44)

In [215]:
# merged_ahs[merged_ahs["County Name"] == "Morgan"]["MeasureId"].value_counts()
# merged_ah[merged_ah["County"] == "Morgan"]["MeasureId"].value_counts()
merged_ah["County"].value_counts()
merged_ahs["County"].value_counts()

Jefferson     2280
Fayette        984
Campbell       300
Warren         288
Daviess        276
Hardin         264
Boone          252
Pike           228
Christian      216
McCracken      204
Bullitt        204
Pulaski        168
Oldham         168
Boyd           156
Henderson      132
Bell           108
Jessamine      108
Greenup        108
Perry           96
Carter          84
Morgan          60
Simpson         48
Hancock         36
Edmonson        36
Trigg           36
Washington      36
Livingston      24
Name: County, dtype: int64

Jefferson     6840
Fayette        984
Campbell       300
Warren         288
Daviess        276
Hardin         264
Boone          252
Pike           228
Christian      216
McCracken      204
Bullitt        204
Pulaski        168
Oldham         168
Boyd           156
Bell           108
Jessamine      108
Greenup        108
Perry           96
Carter          84
Morgan          60
Simpson         48
Hancock         36
Edmonson        36
Trigg           36
Washington      36
Livingston      24
Name: County, dtype: int64

<div class = "alert alert-block alert-warning">
<b>MERGING ON GEOLOCATION </b>    
</div>

In [217]:
# Creating required columns and adjusting type:
import re
merged_ahs['health_long'] = [re.split(' |\(|\)', x)[2] for x in merged_ahs.Geolocation]
merged_ahs['health_lat'] = [re.split(' |\(|\)', x)[3] for x in merged_ahs.Geolocation]
merged_ahs["health_long"] = merged_ahs["health_long"].astype(float)
merged_ahs["health_lat"] = merged_ahs["health_lat"].astype(float)
merged_ahs["so2_long"] = merged_ahs["so2_long"].astype(float)
merged_ahs["so2_lat"] = merged_ahs["so2_lat"].astype(float)

In [218]:
from math import radians, cos, sin, asin, sqrt

def haversine(lon1, lat1, lon2, lat2):

    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # haversine formula 
    dlon = lon2 - lon1 
    dlat = lat2 - lat1 
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a)) 
    r = 3956    # 6371 Radius of earth in kilometers. Use 3956 for miles
    return c * r

merged_ahs['dist'] = merged_ahs.apply(lambda row: haversine(row['health_long'], 
                                            row['health_lat'], 
                                            row['so2_long'], 
                                            row['so2_lat']), axis=1)

merged_ahs[['health_long', "health_lat", "so2_long", "so2_lat", "dist"]]

health_long  health_lat  so2_long   so2_lat       dist
0       -83.531962   36.735278 -83.73694  36.60843  14.337457
1       -83.531962   36.735278 -83.73694  36.60843  14.337457
2       -83.818299   36.668053 -83.73694  36.60843   6.104543
3       -83.766542   36.597588 -83.73694  36.60843   1.803511
4       -83.764845   36.641673 -83.73694  36.60843   2.767545
...            ...         ...       ...       ...        ...
11323   -85.133113   37.839756 -85.04850  37.70460  10.411938
11324   -85.267615   37.718270 -85.04850  37.70460  12.005603
11325   -85.267615   37.718270 -85.04850  37.70460  12.005603
11326   -85.267615   37.718270 -85.04850  37.70460  12.005603
11327   -85.133113   37.839756 -85.04850  37.70460  10.411938

[11328 rows x 5 columns]

<div class = 'alert alert-block alert-warning'>
    SET THRESHOLD FOR distance: Current is 15 <br>
    Mention caveats <br>
    </div>

In [220]:
# merged_ahs["precise"] = (merged_ahs["dist"] < 15)
# We can make it more precise by 1700 rows?
merged_ahs["precise"].value_counts()

True     9636
False    1692
Name: precise, dtype: int64

In [227]:
# reformat our data as GeoPandas DF
crs = {'init': 'EPSG:4326'}
health_geometry = [Point(longlat) for longlat in zip(merged_ahs['health_long'], merged_ahs['health_lat'])]
geo_merged = gpd.GeoDataFrame(merged_ahs, crs = crs, geometry = health_geometry)
geo_merged.rename(columns={"geometry": "health_geometry"}, inplace= True)

so2_geometry = [Point(longlat) for longlat in zip(merged_ahs['so2_long'], merged_ahs['so2_lat'])]
geo_merged = gpd.GeoDataFrame(geo_merged, crs = crs, geometry = so2_geometry)
geo_merged.rename(columns={"geometry": "so2_geometry"}, inplace= True)
geo_merged.head()

C:\Users\Sanha Tahir\anaconda3\envs\my-env\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
C:\Users\Sanha Tahir\anaconda3\envs\my-env\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


index_air     State County  Year_air  Days with AQI  Good Days  Moderate Days  Unhealthy for Sensitive Groups Days  Unhealthy Days  Very Unhealthy Days  Hazardous Days  Max AQI  90th Percentile AQI  Median AQI  Days CO  Days NO2  Days Ozone  Days PM2.5  Days PM10  index_health  Year_health CountyName  CountyFIPS               Category                                            Measure Data_Value_Unit   Data_Value_Type  Data_Value TotalPopulation                       Geolocation   LocationID   MeasureId County Name  Site Num   so2_lat  so2_long  so2_n_dates  so2_good_days  so2_moderate_days  so2_unhealthy_days  so2_unhealthy_sens_days  so2_avg_aqi  so2_max_aqi  so2_min_AQI  health_long  health_lat       dist  precise             health_geometry             health_geometry             health_geometry                so2_geometry
0        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        774350         2019       Bell       21013        Health Outcomes            Depression among adults aged >=18 years               %  Crude prevalence        30.6           1,896  POINT (-83.53196181 36.73527758)  21013960400  DEPRESSION        Bell         2  36.60843 -83.73694          246            228                 12                   6                        0    38.455285           77           14   -83.531962   36.735278  14.337457     True  POINT (-83.53196 36.73528)  POINT (-83.53196 36.73528)  POINT (-83.53196 36.73528)  POINT (-83.73694 36.60843)
1        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809745         2019       Bell       21013          Health Status  Physical health not good for >=14 days among a...               %  Crude prevalence        25.1           1,896  POINT (-83.53196181 36.73527758)  21013960400       PHLTH        Bell         2  36.60843 -83.73694          246            228                 12                   6                        0    38.455285           77           14   -83.531962   36.735278  14.337457     True  POINT (-83.53196 36.73528)  POINT (-83.53196 36.73528)  POINT (-83.53196 36.73528)  POINT (-83.73694 36.60843)
2        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809818         2019       Bell       21013  Health Risk Behaviors       Current smoking among adults aged >=18 years               %  Crude prevalence        33.3           3,139  POINT (-83.81829927 36.66805338)  21013961100    CSMOKING        Bell         2  36.60843 -83.73694          246            228                 12                   6                        0    38.455285           77           14   -83.818299   36.668053   6.104543     True  POINT (-83.81830 36.66805)  POINT (-83.81830 36.66805)  POINT (-83.81830 36.66805)  POINT (-83.73694 36.60843)
3        326  Kentucky   Bell      2019            263        243             20                                    0               0                    0               0       77                   49          39        0         0         234          29          0        809827         2019       Bell       21013             Prevention  Visits to doctor for routine checkup within th...               %  Crude prevalence        80.7           4,747  POINT (-83.76654247 36.59758829)  21013960600     CHECKUP        Bell         2  36.60843 -83.73694          246            228                 12                   6               

In [248]:
import os
import geopandas as gpd
import plotly.graph_objects as go


## SHP FILE
# Unzipping and getting shape files
# C:\Users\Sanha Tahir\Downloads\GeorgeTown\Data Science I\Assignment 4\ShapeFiles\tl_2019_13_cousub
filename = "C:\\Users\\Sanha Tahir\\Downloads\\GeorgeTown\\Data Science I\\Assignment 4\\ShapeFiles\\tl_2019_13_cousub.shp"
map2 = gpd.read_file(filename)
# # Projects it onto a map:
# map2.to_crs(epsg = 4326).plot()


## DATA FILE
# reformat our health data as GeoPandas DF
crs = {'init': 'EPSG:4326'}
health_geometry = [Point(longlat) for longlat in zip(merged_ahs['health_long'], merged_ahs['health_lat'])]
geo_df = gpd.GeoDataFrame(merged_ahs, crs = crs, geometry = health_geometry)

so2_geometry = [Point(longlat) for longlat in zip(geo_df['so2_long'], geo_df['so2_lat'])]
geo_df = gpd.GeoDataFrame(geo_df, crs = crs, geometry = so2_geometry)


#px.set_mapbox_access_token(open(".mapbox_token").read())
fig = go.Figure(data = go.Scattergeo(lon = geo_df["health_long"], 
                                     lat = geo_df["health_lat"], 
                                     text = geo_df["MeasureId"], 
                                     mode = "markers"))

fig.add_scattergeo(lon = geo_df["so2_long"], 
                                     lat = geo_df["so2_lat"], 
                                     text = geo_df["County"], 
                                     mode = "markers",
                                    fillcolor = "rgb(255, 0, 0)")


fig = fig.update_layout(title = "Emission Measure Location & Health Effects", geo_scope = 'usa')

fig.show()

C:\Users\Sanha Tahir\anaconda3\envs\my-env\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6

C:\Users\Sanha Tahir\anaconda3\envs\my-env\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning:

'+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6



In [247]:

fig2 = go.Figure(go.Scattergeo());



fig2.add_scattergeo(lat = geo_df["health_lat"],
                   lon = geo_df["health_long"],
                   marker_size = 5,
                   marker_color = 'rgb(65, 105, 225)' # blue
                     );


fig2.add_scattergeo(lat = geo_df["so2_lat"],
                   lon = geo_df["so2_long"],
                   marker_size = 10,
                   fillcolor = 'rgb(255, 0, 0)'
                     );



fig2 = fig2.update_layout(title = "Source of Emission & Health Effects", geo_scope = 'usa');

fig2.show()